In [17]:
import json
from transformers import GPT2LMHeadModel, GPT2Tokenizer, get_scheduler
import torch
from torch.utils.data import DataLoader, Dataset

from peft import get_peft_model, LoraConfig
from sentence_transformers import SentenceTransformer, util

from nltk.translate.bleu_score import sentence_bleu

! pip install rouge-score nltk
from rouge_score import rouge_scorer

import numpy as np

from itertools import product

In [18]:
# import os
# os.chdir('C:/Users/reese/OneDrive/Documents/MIDS/Fall 2024/DATASCI 266/Final/Data')

from google.colab import drive
drive.mount('/content/drive/')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [19]:
# Load the JSON data
with open('/content/drive/My Drive/w266 Final Project/data/Elvis_cleaned_songs.json', 'r') as file: #Choose between Johhny Cash, Adele, Elvis
    songs = json.load(file)

# Combine all lyrics into a single string
lyrics_data = "\n\n".join([song['lyrics'] for song in songs if song['lyrics'] is not None])
print(f"Total length of lyrics data: {len(lyrics_data)} characters")

# Split the lyrics data into smaller chunks
chunk_size = 1024  # Keep chunk size within 1024 tokens
lyrics_chunks = [lyrics_data[i:i + chunk_size] for i in range(0, len(lyrics_data), chunk_size)]

Total length of lyrics data: 389230 characters


In [20]:
# Load pre-trained model and tokenizer
model_name = 'gpt2'
tokenizer = GPT2Tokenizer.from_pretrained(model_name)
model = GPT2LMHeadModel.from_pretrained(model_name)

In [21]:
# Configure LoRA adaptation
config = LoraConfig(r = 12, lora_alpha = 16, lora_dropout = 0.25)
model = get_peft_model(model, config)

In [22]:
# Tokenize each chunk
tokenized_inputs = []
for chunk in lyrics_chunks:
    inputs = tokenizer(chunk, return_tensors='pt', max_length=1024, truncation=True)
    tokenized_inputs.append(inputs)

print(f"Number of chunks processed: {len(tokenized_inputs)}")

Number of chunks processed: 381


In [23]:
# Prepare Dataset and DataLoader
class LyricsDataset(Dataset):
    def __init__(self, input_ids):
        self.input_ids = input_ids

    def __len__(self):
        return len(self.input_ids)

    def __getitem__(self, idx):
        return self.input_ids[idx], self.input_ids[idx]

# Flatten tokenized inputs for Dataset
flattened_input_ids = [item['input_ids'].squeeze() for item in tokenized_inputs]
dataset = LyricsDataset(flattened_input_ids)
dataloader = DataLoader(dataset, batch_size = 1, shuffle = True)

In [24]:
# Fine-Tune the GPT-2 Model with LoRA
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)
model.train()

#gradient_accumulation_steps = 4  # Combine gradients over multiple steps
optimizer = torch.optim.AdamW(model.parameters(), lr = 1.5e-5, weight_decay = 0.01)

epoch = 8

#num_training_steps = len(dataloader) * epoch
#scheduler = get_scheduler("linear", optimizer=optimizer, num_warmup_steps=0, num_training_steps=num_training_steps)

for e in range(epoch):  # Example: 3 epochs
    for batch in dataloader:
        input_ids, labels = batch
        input_ids, labels = input_ids.to(device), labels.to(device)

        optimizer.zero_grad()
        outputs = model(input_ids, labels=labels)
        loss = outputs.loss
        loss.backward()
        optimizer.step()

        print(f"Epoch {e+1} Loss: {loss.item()}")

Epoch 1 Loss: 2.1728382110595703
Epoch 1 Loss: 4.16669225692749
Epoch 1 Loss: 3.3425822257995605
Epoch 1 Loss: 4.401546955108643
Epoch 1 Loss: 3.4726741313934326
Epoch 1 Loss: 3.4364538192749023
Epoch 1 Loss: 3.6980397701263428
Epoch 1 Loss: 2.6296942234039307
Epoch 1 Loss: 3.739318609237671
Epoch 1 Loss: 2.416532516479492
Epoch 1 Loss: 3.283341884613037
Epoch 1 Loss: 1.8607096672058105
Epoch 1 Loss: 3.048149824142456
Epoch 1 Loss: 2.6491081714630127
Epoch 1 Loss: 3.2144973278045654
Epoch 1 Loss: 3.4162986278533936
Epoch 1 Loss: 3.892127275466919
Epoch 1 Loss: 3.7208547592163086
Epoch 1 Loss: 3.3161096572875977
Epoch 1 Loss: 3.622868537902832
Epoch 1 Loss: 4.132956504821777
Epoch 1 Loss: 2.524078369140625
Epoch 1 Loss: 3.7230005264282227
Epoch 1 Loss: 3.4728310108184814
Epoch 1 Loss: 2.665658950805664
Epoch 1 Loss: 3.822084903717041
Epoch 1 Loss: 3.0581767559051514
Epoch 1 Loss: 2.785801649093628
Epoch 1 Loss: 2.208956003189087
Epoch 1 Loss: 3.466505765914917
Epoch 1 Loss: 3.5225229263

In [25]:
# Generate New Lyrics with the LoRA-adapted Model
model.eval()

PeftModel(
  (base_model): LoraModel(
    (model): GPT2LMHeadModel(
      (transformer): GPT2Model(
        (wte): Embedding(50257, 768)
        (wpe): Embedding(1024, 768)
        (drop): Dropout(p=0.1, inplace=False)
        (h): ModuleList(
          (0-11): 12 x GPT2Block(
            (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
            (attn): GPT2SdpaAttention(
              (c_attn): lora.Linear(
                (base_layer): Conv1D(nf=2304, nx=768)
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.25, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=768, out_features=12, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=12, out_features=2304, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
               

In [26]:
# Load the pre-trained Sentence-BERT model
STS_model = SentenceTransformer('all-MiniLM-L6-v2')

# Semantic similarity calculation
def compute_semantic_similarity(generated_lyrics, reference_lyrics):
    # Encode the sentences into embeddings
    generated_embedding = STS_model.encode(generated_lyrics, convert_to_tensor=True)
    reference_embedding = STS_model.encode(reference_lyrics, convert_to_tensor=True)

    # Compute cosine similarity between the embeddings
    similarity_score = util.pytorch_cos_sim(generated_embedding, reference_embedding)
    return similarity_score.item()

In [27]:
# BLEU score calculation
def compute_bleu_score(generated_lyrics, reference_lyrics):
    reference_tokens = reference_lyrics.split()  # Tokenize the reference lyrics
    generated_tokens = generated_lyrics.split()  # Tokenize the generated lyrics
    bleu_score = sentence_bleu([reference_tokens], generated_tokens)  # Compute BLEU score
    return bleu_score

In [28]:
# ROUGE score calculation
def compute_rouge_score(generated_lyrics, reference_lyrics):
    scorer = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)
    scores = scorer.score(reference_lyrics, generated_lyrics)
    return scores

In [16]:
# Define parameter grid
param_grid = {
    "top_k": [10, 20, 30],
    "top_p": [0.6, 0.7, 0.8, 0.9],
    "temperature": [0.6, 0.7, 0.9],
}

# Generate all combinations of parameters
param_combinations = list(product(
    param_grid["top_k"],
    param_grid["top_p"],
    param_grid["temperature"],
))

In [14]:
# Initialize variables
best_params = None
best_score = -float("inf")
results = []

prompts = [song['lyrics'].split('\n')[1] for song in songs if song['lyrics'] is not None]
reference_lyrics = [song['lyrics'] for song in songs if song['lyrics'] is not None]

# # Ensure pad_token is properly defined
# if tokenizer.pad_token is None:
#     tokenizer.add_special_tokens({'pad_token': '[PAD]'})  # Add custom pad token if not present
#     model.resize_token_embeddings(len(tokenizer))  # Resize model embeddings to include new token

# # Set `pad_token_id` to the integer ID of the pad token
# tokenizer.pad_token_id = tokenizer.eos_token_id if tokenizer.pad_token_id is None else tokenizer.pad_token_id
# model.config.pad_token_id = tokenizer.pad_token_id  # Ensure consistency

# Iterate through parameter combinations
for top_k, top_p, temperature in param_combinations:
    print(f"Testing parameters: top_k={top_k}, top_p={top_p}, temperature={temperature}")

    semantic_similarities = []
    bleu_scores = []
    rouge1_scores = []
    rouge2_scores = []
    rougeL_scores = []

    # Evaluate each prompt
    for i, prompt in enumerate(prompts):
        if not prompt.strip():  # Check if prompt is empty or contains only whitespace
            continue  # Skip empty prompts

        # Generate text
        input_ids = tokenizer(prompt, return_tensors='pt').input_ids.to(device)
        output_ids = model.generate(input_ids,
                                    max_length=500,
                                    num_return_sequences=1,
                                    no_repeat_ngram_size=2,
                                    top_k=top_k,
                                    top_p=top_p,
                                    temperature=temperature,
                                    early_stopping=True,

                                    # pad_token_id = tokenizer.pad_token,
                                    do_sample = True) #to allow varied outputs, negating decoding strategies like beam search / greedy decoding

        generated_text = tokenizer.decode(output_ids[0], skip_special_tokens=True)

        # Compute metrics
        semantic_score = compute_semantic_similarity(generated_text, reference_lyrics[i])
        bleu_score = compute_bleu_score(generated_text, reference_lyrics[i])
        rouge_scores = compute_rouge_score(generated_text, reference_lyrics[i])

        # Collect scores
        semantic_similarities.append(semantic_score)
        bleu_scores.append(bleu_score)
        rouge1_scores.append(rouge_scores["rouge1"].fmeasure)
        rouge2_scores.append(rouge_scores["rouge2"].fmeasure)
        rougeL_scores.append(rouge_scores["rougeL"].fmeasure)

    # Compute averages
    avg_semantic_similarity = np.mean(semantic_similarities)
    avg_bleu = np.mean(bleu_scores)
    avg_rouge1 = np.mean(rouge1_scores)
    avg_rouge2 = np.mean(rouge2_scores)
    avg_rougeL = np.mean(rougeL_scores)

    print(f"Semantic Similarity Score: {avg_semantic_similarity}")

    # Log results
    results.append({
        "params": {"top_k": top_k, "top_p": top_p, "temperature": temperature},
        "semantic_similarity": avg_semantic_similarity,
        "bleu": avg_bleu,
        "rouge1": avg_rouge1,
        "rouge2": avg_rouge2,
        "rougeL": avg_rougeL
    })

    # Update best parameters
    if avg_semantic_similarity > best_score:
        best_score = avg_semantic_similarity
        best_params = {"top_k": top_k, "top_p": top_p, "temperature": temperature}

# Display best results
print(f"Best Parameters: {best_params}")
print(f"Best Semantic Similarity: {best_score}")

# Display all results
for res in results:
    print(f"Params: {res['params']} -> Semantic: {res['semantic_similarity']}, BLEU: {res['bleu']}, ROUGE-1: {res['rouge1']}, ROUGE-2: {res['rouge2']}, ROUGE-L: {res['rougeL']}")


/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:638: UserWarning: `num_beams` is set to 1. However, `early_stopping` is set to `True` -- this flag is only used in beam-based generation modes. You should set `num_beams>1` or unset `early_stopping`.
  warnings.warn(
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


Testing parameters: top_k=10, top_p=0.6, temperature=0.6


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
/usr/local/lib/python3.10/dist-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reli

Semantic Similarity Score: 0.4670841196976585
Testing parameters: top_k=10, top_p=0.6, temperature=0.7


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


...

Semantic Similarity Score: 0.4606132783189113
Testing parameters: top_k=30, top_p=0.9, temperature=0.7


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


Semantic Similarity Score: 0.4513495603942104
Testing parameters: top_k=30, top_p=0.9, temperature=0.9


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


Semantic Similarity Score: 0.4374880984080766
Best Parameters: {'top_k': 20, 'top_p': 0.6, 'temperature': 0.6}
Best Semantic Similarity: 0.4750727637025526
Params: {'top_k': 10, 'top_p': 0.6, 'temperature': 0.6} -> Semantic: 0.4670841196976585, BLEU: 0.028675190871795084, ROUGE-1: 0.2775034744025242, ROUGE-2: 0.06922690215176915, ROUGE-L: 0.15950657316594774
Params: {'top_k': 10, 'top_p': 0.6, 'temperature': 0.7} -> Semantic: 0.4683520936241066, BLEU: 0.027778107962047355, ROUGE-1: 0.2741233959366277, ROUGE-2: 0.06657617219670706, ROUGE-L: 0.15515754475730112
Params: {'top_k': 10, 'top_p': 0.6, 'temperature': 0.9} -> Semantic: 0.468347862808551, BLEU: 0.027966700376430596, ROUGE-1: 0.27410312166129625, ROUGE-2: 0.06595697489241954, ROUGE-L: 0.15525523487534199
Params: {'top_k': 10, 'top_p': 0.7, 'temperature': 0.6} -> Semantic: 0.4650185464736301, BLEU: 0.027347425234765726, ROUGE-1: 0.27142955287174947, ROUGE-2: 0.06492516404323842, ROUGE-L: 0.15476874203248003
Params: {'top_k': 10, '

In [30]:
# Prompt for generation
prompt = "When a boy like me meets a girl like you"
input_ids = tokenizer(prompt, return_tensors='pt').input_ids.to(device)

# Generate lyrics - you can change max_length to getlonger songs
output_ids = model.generate(input_ids,
                            max_length=500,
                            num_return_sequences=1,
                            no_repeat_ngram_size=2,
                            top_k = best_params['top_k'],
                            top_p = best_params['top_p'],
                            temperature = best_params['temperature'],
                            early_stopping = True,
                            do_sample = True)
# Decode and print
generated_lyrics = tokenizer.decode(output_ids[0], skip_special_tokens=True)
print(generated_lyrics)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


When a boy like me meets a girl like you, she'll be the one who will love you forever.

[Verse 1]
I'll never forget you
You're my only hope
Don't let me down
Oh, I'll always remember you and I will always love
And I'm going to keep you safe
(Chorus)
Well, you're going out of your way to be my best friend
But I know you'll come back
When I tell you I love to see you again
Cause I've been waiting for you to come
Until I say goodbye
So, don't worry, just keep going
Baby, stay with me
Keep going, baby
Stay with you baby, keep coming
Always keep on going baby baby (Choruses) (Verb) [Verbs 1-3] (I'm so sorry, but I don' know what I want to do] [Choral] I hope you don
Like I said, when I was young,
My parents were all the same
They were the ones who taught me to love and be happy
Because they taught my mother to take care of me and make me happy. (Guitar) I wish I could say that I loved you all
Even though I didn't know how to sing
It was always so hard to hear you sing, and you always made m